## This Notebook calculates the powerspektrum for various diffrent cosmological starting parameters

In [1]:
import socket
socket.gethostname()

'euclid.uibk.ac.at'

In [1]:
import pyccl as ccl
import g3lhalo
import matplotlib.pyplot as plt
import numpy as np
from pyDOE import lhs
import tensorflow as tf
import matplotlib.pyplot as plt
import json
import os
from datetime import datetime

2025-04-22 12:24:40.585454: I tensorflow/core/util/port.cc:110] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-04-22 12:24:41.677495: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-22 12:24:42.529037: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-22 12:24:42.529971: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI AVX512_BF16 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-04-22 12:24:54.326704: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT

In [ ]:
#%pip install pyDOE

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [3]:
# checking that we are using a GPU
device = 'gpu:0' if tf.test.is_gpu_available() else 'cpu'
print('using', device, 'device \n')

Instructions for updating:
Use `tf.config.list_physical_devices('GPU')` instead.
using cpu device 



In [4]:
# setting the seed for reproducibility
np.random.seed(9721)
tf.random.set_seed(9721)

## Calculating dataset

In [ ]:
N_total = 50000
num_params = 10

data_array = np.empty((N_total, num_params), dtype=object)

Mth_min = 1e10
Mth_max = 1e15
param_intervals = {
    'Om_c': (0.1, 0.6),
    'Om_b': (0.04, 0.06),
    'h': (0.64, 0.82),
    'sigma_8': (0.8, 1),
    'n_s': (0.84, 1.1),
    'alpha': (0, 1),
    'sigma': (0.01, 1),
    'Mth': (Mth_min, Mth_max),
    'Mprime': (Mth_min * 1, Mth_max * 100),
    'beta': (0.1, 2)
}

# Anzahl der Parameter (Dimensionen des LHS)
num_cosmo_params = len(param_intervals)

# Generiere Latin Hypercube Samples (LHS)
lhs_samples = lhs(num_cosmo_params, samples=N_total)

# Skaliere die LHS-Samples auf die jeweiligen Intervalle
cosmo_samples = []
for sample in lhs_samples:
    cosmo = {
        key: param_intervals[key][0] + (param_intervals[key][1] - param_intervals[key][0]) * sample[i]
        for i, key in enumerate(param_intervals)
    }
    cosmo_samples.append(cosmo)

# Halo mass function
hmf = ccl.halos.MassFuncSheth99()

# Halo bias
hbf = ccl.halos.HaloBiasSheth01()

# Concentration mass Relation
cmfunc = ccl.halos.ConcentrationDuffy08()

# Korrelation zwischen Galaxienpopulationen
A = 0  # 0 ==> Keine Korrelation zwischen Populationen
epsilon = 0

# Skalierung des Halo-Profils
flens = 1  # 1 ==> Gleiches Profil wie dunkle Materie

data_array = []

Pk_ss_1h = [1] * 50  # Platzhalter für die 50 Werte
Pk_ss_2h = [2] * 50
Pk_ss = [3] * 50
Pk_sl_1h = [4] * 50
Pk_sl_2h = [5] * 50
Pk_sl = [6] * 50
Pk_ll_1h = [7] * 50
Pk_ll_2h = [8] * 50
Pk_ll = [9] * 50
Pk_lin = [10] * 50

# Hauptschleife für Simulationen
for i in range(N_total):
    # Kosmologische Parameter aus LHS entnehmen
    cosmo = cosmo_samples[i]
    cosmo_array = np.array(list(cosmo.values()))

    # Nur die 5 kosmologischen Parameter für das Modell extrahieren
    cosmo_subset = {
        key: cosmo[key] for key in ['Om_c', 'Om_b', 'h', 'sigma_8', 'n_s']
    }

    # HOD-Parameter extrahieren
    alpha = cosmo['alpha']
    sigma = cosmo['sigma']
    Mth = cosmo['Mth']
    Mprime = cosmo['Mprime']
    beta = cosmo['beta']


    # HOD abrufen
    hod_cen, hod_sat = g3lhalo.HOD_Zheng(alpha, Mth, sigma, Mprime, beta)

    # Modell definieren
    model = g3lhalo.halomodel(verbose=True, cosmo=cosmo_subset, hmfunc=hmf, hbfunc=hbf, cmfunc=cmfunc)
    model.set_hods(hod_cen, hod_sat, A=A, epsilon=epsilon, flens1=flens, flens2=flens)

    # Berechnungen durchführen
    ks = np.geomspace(1e-2, 1e2)
    z = 0

    # Lineares Materie-Leistungsspektrum
    Pk_lin = model.pk_lin(ks, z)

    # Materie-Materie Leistungsspektrum
    Pk_ss_1h, Pk_ss_2h, Pk_ss = model.source_source_ps(ks, z)

    # Materie-Galaxie Leistungsspektrum
    Pk_sl_1h, Pk_sl_2h, Pk_sl = model.source_lens_ps(ks, z, type=1)

    # Galaxie-Galaxie Leistungsspektrum
    Pk_ll_1h, Pk_ll_2h, Pk_ll = model.lens_lens_ps(ks, z, type1=1, type2=1)
    

    # Erstelle das Dictionary mit den Daten für das aktuelle Sample
    data_dict = {
        'Pk_ss_1h': Pk_ss_1h,
        'Pk_ss_2h': Pk_ss_2h,
        'Pk_ss': Pk_ss,
        'Pk_sl_1h': Pk_sl_1h,
        'Pk_sl_2h': Pk_sl_2h,
        'Pk_sl': Pk_sl,
        'Pk_ll_1h': Pk_ll_1h,
        'Pk_ll_2h': Pk_ll_2h,
        'Pk_ll': Pk_ll,
        'Pk_lin': Pk_lin,
    }
    
    # Füge das Dictionary für dieses Sample der Liste hinzu
    data_array.append(data_dict)

    print(f"Run {i+1}/{N_total} completed")


Setting cosmology
Om_c: 0.13892533720323125
Om_b: 0.02221794071928906
h: 0.704792072349252
sigma_8: 0.9009708783644712
n_s: 0.9637751092996931
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 1/10000 completed
Setting cosmology
Om_c: 0.152485797525424
Om_b: 0.019363072099307276
h: 0.6790845166338463
sigma_8: 0.9839206177615446
n_s: 1.0763682429606474
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 2/10000 completed
Setting cosmology
Om_c: 0.13424256091119546
Om_b: 0.021240947012867613
h: 0.7358118774691687
sigma_8: 0.9375353490634569
n_s: 0.9410637691565839
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 3/10000 completed
Setting cosmology
Om_c: 0.1967347800902421
Om_b: 0.0210127689120615
h: 0.645989054864696
sigma_8: 0.9391298

/home/rhoffmann/.local/lib/python3.10/site-packages/g3lhalo/halomodel.py:508: IntegrationWarning: The algorithm does not converge.  Roundoff error is detected
  in the extrapolation table.  It is assumed that the requested tolerance
  cannot be achieved, and that the returned result (if full_output = 1) is 
  the best which can be obtained.
  A = integrate.quad(kernel_A, mmin, mmax, epsrel=epsrel)[0]


Run 1769/10000 completed
Setting cosmology
Om_c: 0.0813581810047643
Om_b: 0.021429983559026044
h: 0.7472745724998723
sigma_8: 0.9387269555741526
n_s: 0.8597224708164709
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 1770/10000 completed
Setting cosmology
Om_c: 0.06221124129359353
Om_b: 0.02499430137963047
h: 0.7281079353311889
sigma_8: 0.830486169248427
n_s: 0.8789626446677042
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 1771/10000 completed
Setting cosmology
Om_c: 0.08432326377997332
Om_b: 0.025376033344529147
h: 0.8182742773456082
sigma_8: 0.8707464436033951
n_s: 0.8593543457435393
Also setting linear matter power spectrum
Setting halo mass function
Setting halo bias function
Setting concentration mass relation
Run 1772/10000 completed
Setting cosmology
Om_c: 0.14538706548868585
Om_b: 0.018846208956398148
h

## Saving generated data

In [6]:
# Funktion, die rekursiv alle np.ndarrays in Listen umwandelt
def convert_to_serializable(obj):
    if isinstance(obj, np.ndarray):
        return obj.tolist()  # Umwandlung in eine Python-Liste
    elif isinstance(obj, list):
        return [convert_to_serializable(item) for item in obj]  # Rekursive Umwandlung der Listenelemente
    elif isinstance(obj, dict):
        return {key: convert_to_serializable(value) for key, value in obj.items()}  # Rekursive Umwandlung der Dictionary-Werte
    else:
        return obj  # Für alle anderen Typen keine Änderung

# Konvertiere alle numpy.ndarrays in data_array
data_array_serializable = [convert_to_serializable(sublist) for sublist in data_array]

# Anzahl der generierten Daten
num_data_points = len(data_array_serializable)

# Verzeichnis für die gespeicherten Daten
data_dir = "../Data/"
os.makedirs(data_dir, exist_ok=True)

# Erzeuge einen einzigartigen Dateinamen mit Zeitstempel
timestamp = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
data_fn = f"{data_dir}/GeneratedData_{num_data_points}_{timestamp}.json"

# Speichern der Daten
with open(data_fn, "w") as json_file:
    json.dump(data_array_serializable, json_file, indent=4)

print(f"Daten erfolgreich gespeichert in: {data_fn}")


Daten erfolgreich gespeichert in: ../Data//GeneratedData_10000_2025-04-22_13-00-44.json


## Saving related parameter

In [7]:
para_fn = f"{data_dir}/Parameter_{num_data_points}_{timestamp}.json"
# Speichern der Daten
with open(para_fn, "w") as json_file:
    json.dump(cosmo_samples, json_file, indent=4)

print(f"Daten erfolgreich gespeichert in: {data_fn}")

Daten erfolgreich gespeichert in: ../Data//GeneratedData_10000_2025-04-22_13-00-44.json
